In [3]:
from datasets import load_dataset
import pandas as pd 
from pymongo import MongoClient
from transformers import BertTokenizer, BertForMaskedLM, DPRContextEncoderTokenizer,DPRContextEncoder;
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
import re
import pandas as pd
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords as nltk_stopwords
from transformers import BertTokenizer, BertModel, AutoTokenizer
from sklearn.metrics.pairwise import cosine_similarity
import torch
from pymongo import MongoClient
import torch.nn.functional as F

In [18]:
import pandas as pd
import re
from transformers import AutoTokenizer
import spacy
import stanza

# ------------------------Cümlelerin boyutlarını ve stop words'leri tanımladığımız yer-----------------------------
# Yüklediğiniz modele göre değiştirebilirsiniz
nlp = stanza.Pipeline('tr')

def preprocess_text(text):
    doc = nlp(text)
    tokens = [token.lemma_ for token in doc if not token.is_stop and not token.is_punct]
    return " ".join(tokens)

def extract_keywords_and_subheadings(text):
    doc = nlp(text)
    keywords = []
    subheadings = []
    for ent in doc.ents:
        if ent.label_ == "ORG" or ent.label_ == "PERSON":  # Örnek: Kurum veya kişi isimleri
            keywords.append(ent.text)
        elif ent.label_ == "GPE":  # Örnek: Yer isimleri
            subheadings.append(ent.text)
    return keywords, subheadings

def truncate_text_meaningful(text, max_len=300):
    # Önce metni tokenlere ayır
    doc = nlp(text)

    # Stop kelimeleri ve noktalama işaretlerini kaldır
    tokens = [token.lemma_ for token in doc if not token.is_stop and not token.is_punct]

    # Belirli bir uzunluktaki metni döndür
    truncated_text = ' '.join(tokens[:max_len])

    return truncated_text

# ----------------------------------Tokenize etme fonksiyonu-----------------------------------
def tokenize_and_pad(data, model_name='bert-base-uncased', max_length=512):
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    encoded_input = tokenizer(data, padding=True, truncation=True, max_length=max_length)
    return encoded_input

class DataProcessor:
    def __init__(self, input_csv, output_csv, max_words=300, model_name='dbmdz/distilbert-base-turkish-cased'):
        self.input_csv = input_csv
        self.output_csv = output_csv
        self.max_words = max_words
        self.model_name = model_name

    def main_pipeline(self):
        def filter_text(text):
            # Dış bağlantılar ve kaynakçaları kaldır
            text = re.sub(r'http\S+|https\S+|\b(?:www\.)?\S+\.\w{2,4}\b', '', text)
            # Tarih ve sayıları kaldır
            text = re.sub(r'\d{4}-\d{2}-\d{2}|\d{2}/\d{2}/\d{4}|\d+', '', text)
            # Sayıları kaldır
            text = re.sub(r'\d+', '', text)
            # Kısa veya uzun kelimeleri kaldır
            words = text.split()
            words = [word for word in words if 2 <= len(word) <= 20]
            return ' '.join(words)
        
        # UTF-8 encoding ile dosyayı okuyun
        df = pd.read_csv(self.input_csv, encoding='utf-8')
        
        # Metinlerin sütun adını kontrol edin
        if 'metinler' not in df.columns:
            raise ValueError("CSV dosyasında 'metinler' adlı bir sütun bulunamadı. Lütfen sütun adını kontrol edin.")
        
        df['kısaltılmıs_metin'] = df['metinler'].apply(filter_text)

        # Metinleri kısalt
        df['kısaltılmıs_metin'] = df['metinler'].apply(lambda x: truncate_text_meaningful(x, max_len=self.max_words))

        # Tokenize et ve padding uygula
        padded_tokens = tokenize_and_pad(df['kısaltılmıs_metin'].tolist(), model_name=self.model_name)
        df['padded_tokens'] = padded_tokens['input_ids']

        print("Kısaltılmış metinler:")
        print(df['kısaltılmıs_metin'].head())
        print("Tokenize edilmiş ve padding uygulanmış veriler:")
        print(df[['kısaltılmıs_metin', 'padded_tokens']].head())

        # Veriyi kaydet
        self.save_cleaned_data(df)
    
    def save_cleaned_data(self, df):
        df.to_csv(self.output_csv, index=False, encoding='utf-8')
        print(f"Temizlenmiş veri '{self.output_csv}' dosyasına kaydedildi.")

# ---------------------------------Verilerin kaydedilmesi-------------------------------------
processor = DataProcessor(input_csv="texts_egitim.csv", output_csv="cleaned_data4.csv")
processor.main_pipeline()


2024-08-27 17:58:58 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


2024-08-27 17:58:58 INFO: Downloaded file to C:\Users\info\stanza_resources\resources.json
2024-08-27 17:58:59 INFO: Loading these models for language: tr (Turkish):
| Processor | Package       |
-----------------------------
| tokenize  | imst          |
| mwt       | imst          |
| pos       | imst_charlm   |
| lemma     | imst_nocharlm |
| depparse  | imst_charlm   |
| ner       | starlang      |

2024-08-27 17:58:59 INFO: Using device: cpu
2024-08-27 17:58:59 INFO: Loading: tokenize
c:\gitProjects\yeni\.venv\lib\site-packages\stanza\models\tokenization\trainer.py:82: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped

TypeError: 'Document' object is not iterable

In [4]:
import re
import pandas as pd
from nltk.stem.snowball import SnowballStemmer

# Türkçe stemmer
stemmer = SnowballStemmer("turkish")

def stem_text(text):
    words = text.split()
    stemmed_words = [stemmer.stem(word) for word in words]
    return ' '.join(stemmed_words)

class DataProcessor:
    def __init__(self, input_csv, output_csv, max_words=300, model_name='dbmdz/distilbert-base-turkish-cased'):
        self.input_csv = input_csv
        self.output_csv = output_csv
        self.max_words = max_words
        self.model_name = model_name

    def main_pipeline(self):
        def filter_text(text):
            # Dış bağlantılar ve kaynakçaları kaldır
            text = re.sub(r'http\S+|https\S+|\b(?:www\.)?\S+\.\w{2,4}\b', '', text)
            # Tarih ve sayıları kaldır
            text = re.sub(r'\d{4}-\d{2}-\d{2}|\d{2}/\d{2}/\d{4}|\d+', '', text)
            # Sayıları kaldır
            text = re.sub(r'\d+', '', text)
            # Kısa veya uzun kelimeleri kaldır
            words = text.split()
            words = [word for word in words if 2 <= len(word) <= 20]
            return ' '.join(words)
        
        # UTF-8 encoding ile dosyayı okuyun
        df = pd.read_csv(self.input_csv, encoding='utf-8')

        # Metinleri filtrele
        df['filtered_text'] = df['metinler'].apply(filter_text)

        # Filtrelenmiş metinleri stem (kök) yap
        df['stemmed_text'] = df['filtered_text'].apply(stem_text)

        # Sonuçları yeni bir CSV dosyasına kaydet
        df.to_csv(self.output_csv, index=False, encoding='utf-8')

# Kullanım örneği
processor = DataProcessor(input_csv='texts_egitim.csv', output_csv='cleaned_data4.csv')
processor.main_pipeline()


ValueError: The language 'turkish' is not supported.

In [7]:
import pandas as pd
import re
from transformers import AutoTokenizer
import spacy
import stanza

# ------------------------ Cümlelerin boyutlarını ve stop words'leri tanımladığımız yer -----------------------------
nlp = stanza.Pipeline('tr', processors='tokenize,mwt,pos,lemma,ner')

def preprocess_text(text, stopwords):
    doc = nlp(text)
    tokens = [
        word.lemma if word.lemma is not None else word.text
        for sentence in doc.sentences
        for word in sentence.words
        if word.text.lower() not in stopwords
    ]
    return " ".join(tokens)

def extract_keywords_and_subheadings(text):
    doc = nlp(text)
    keywords = []
    subheadings = []
    for ent in doc.ents:
        if ent.label_ == "ORG" or ent.label_ == "PERSON":  # Örnek: Kurum veya kişi isimleri
            keywords.append(ent.text)
        elif ent.label_ == "GPE":  # Örnek: Yer isimleri
            subheadings.append(ent.text)
    return keywords, subheadings

def truncate_text_meaningful(text, max_len=300):
    doc = nlp(text)
    tokens = [word.lemma if word.lemma is not None else word.text for word in doc.words]
    truncated_text = ' '.join(tokens[:max_len])
    return truncated_text

def tokenize_and_pad(data, model_name='bert-base-uncased', max_length=512):
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    encoded_input = tokenizer(data, padding=True, truncation=True, max_length=max_length)
    return encoded_input

class DataProcessor:
    def __init__(self, input_csv, output_csv, stopword_file, max_words=300, model_name='dbmdz/distilbert-base-turkish-cased'):
        self.input_csv = input_csv
        self.output_csv = output_csv
        self.stopword_file = stopword_file
        self.max_words = max_words
        self.model_name = model_name
        self.stopwords = self.load_stopwords()

    def load_stopwords(self):
        with open(self.stopword_file, 'r', encoding='utf-8') as file:
            stopwords = set(file.read().split())
        return stopwords

    def main_pipeline(self):
        def filter_text(text):
            text = re.sub(r'http\S+|https\S+|\b(?:www\.)?\S+\.\w{2,4}\b', '', text)
            text = re.sub(r'\d{4}-\d{2}-\d{2}|\d{2}/\d{2}/\d{4}|\d+', '', text)
            text = re.sub(r'\d+', '', text)
            words = text.split()
            words = [word for word in words if 2 <= len(word) <= 20]
            return ' '.join(words)
        
        df = pd.read_csv(self.input_csv, encoding='utf-8')
        
        if 'metinler' not in df.columns:
            raise ValueError("CSV dosyasında 'metinler' adlı bir sütun bulunamadı. Lütfen sütun adını kontrol edin.")
        
        df['kısaltılmıs_metin'] = df['metinler'].apply(lambda x: preprocess_text(x, self.stopwords))
        df['kısaltılmıs_metin'] = df['kısaltılmıs_metin'].apply(lambda x: truncate_text_meaningful(x, max_len=self.max_words))

        padded_tokens = tokenize_and_pad(df['kısaltılmıs_metin'].tolist(), model_name=self.model_name)
        df['padded_tokens'] = padded_tokens['input_ids']

        print("Kısaltılmış metinler:")
        print(df['kısaltılmıs_metin'].head())
        print("Tokenize edilmiş ve padding uygulanmış veriler:")
        print(df[['kısaltılmıs_metin', 'padded_tokens']].head())

        self.save_cleaned_data(df)
    
    def save_cleaned_data(self, df):
        df.to_csv(self.output_csv, index=False, encoding='utf-8')
        print(f"Temizlenmiş veri '{self.output_csv}' dosyasına kaydedildi.")

processor = DataProcessor(input_csv="texts_egitim.csv", output_csv="cleaned_data4.csv", stopword_file="gereksiz_kelimeler.txt")
processor.main_pipeline()


2024-08-28 11:26:01 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


2024-08-28 11:26:02 INFO: Downloaded file to C:\Users\info\stanza_resources\resources.json
2024-08-28 11:26:02 INFO: Loading these models for language: tr (Turkish):
| Processor | Package       |
-----------------------------
| tokenize  | imst          |
| mwt       | imst          |
| pos       | imst_charlm   |
| lemma     | imst_nocharlm |
| ner       | starlang      |

2024-08-28 11:26:02 INFO: Using device: cpu
2024-08-28 11:26:02 INFO: Loading: tokenize
c:\gitProjects\yeni\.venv\lib\site-packages\stanza\models\tokenization\trainer.py:82: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the fu

: 

In [ ]:
import pandas as pd
from transformers import AutoModel, AutoTokenizer
import torch
from sklearn.metrics.pairwise import cosine_similarity

# Model ve tokenizer'ı yükleme
model_name = 'dbmdz/distilbert-base-turkish-cased'
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModel.from_pretrained(model_name)

def get_embeddings(text):
    inputs = tokenizer(text, return_tensors='pt', truncation=True, padding=True)
    with torch.no_grad():
        outputs = model(**inputs)
    # İlk özniteliklerin ortalamasını alarak vektör elde etme
    embeddings = outputs.last_hidden_state.mean(dim=1).squeeze()
    return embeddings

def generate_subheadings(title, keywords, top_n=5):
    title_embedding = get_embeddings(title)
    keyword_embeddings = [get_embeddings(keyword) for keyword in keywords]

    similarities = [cosine_similarity(title_embedding.unsqueeze(0), keyword_embedding.unsqueeze(0))[0][0] for keyword_embedding in keyword_embeddings]
    sorted_indices = sorted(range(len(similarities)), key=lambda i: similarities[i], reverse=True)

    # Benzerliklere göre anahtar kelimelerden alt başlıklar oluşturma
    subheadings = [keywords[i] for i in sorted_indices[:top_n]]
    return subheadings

# Örnek veri
title = "Veri Bilimi Nedir?"
keywords = ["Makine Öğrenmesi", "Büyük Veri", "Yapay Zeka", "1936", "Veri Madenciliği", "Derin Öğrenme", "Doğal Dil İşleme", "1982", "Yapay Sinir Ağları", "Kümeleme"]

# Alt başlıkları oluşturma
subheadings = generate_subheadings(title, keywords)
print("Alt Başlıklar:")
for subheading in subheadings:
    print(f"- {subheading}")


In [1]:
import pandas as pd

# CSV dosyasını oku
df = pd.read_csv('cleaned_data.csv')

# Görmek istediğiniz üç sütunu seçin
selected_columns = df[['kısaltılmıs_metin']]

# Seçilen sütunları tablo olarak görüntüle
print(selected_columns)

# Eğer Jupyter Notebook kullanıyorsanız, daha güzel görüntü için display() fonksiyonunu kullanabilirsiniz:
from IPython.display import display
display(selected_columns)


                                        kısaltılmıs_metin
0       W F 295–596 P N 82 3–211 78 pp 137–146 5–537 "...
1       Pasaportunun Ama 1934 Balıkesir'de Doktoru Pro...
2       hesaplamalar ortalarına 2 II Bu kümesi İlk II ...
3       1 20 14 19 12 14 Yazın Türkçedir Zaman geçirmi...
4       " ) inşasıyla ilgilenir "Ters mühendislik, müh...
...                                                   ...
104103  Xenocicerina, Cicerininae altfamilyasına cinsi...
104104  Paracicerina, Cicerininae altfamilyasına cinsi...
104105  Lig futbolcuları Yasin Güreler (d Lig futbolcu...
104106  Elvertia, Kalyptorhynchia seksiyonuna cinsidir...
104107  Kaynakça Ek Hartcher New York: HarperCollins M...

[104108 rows x 1 columns]


kısaltılmıs_metin
0       W F 295–596 P N 82 3–211 78 pp 137–146 5–537 "...
1       Pasaportunun Ama 1934 Balıkesir'de Doktoru Pro...
2       hesaplamalar ortalarına 2 II Bu kümesi İlk II ...
3       1 20 14 19 12 14 Yazın Türkçedir Zaman geçirmi...
4       " ) inşasıyla ilgilenir "Ters mühendislik, müh...
...                                                   ...
104103  Xenocicerina, Cicerininae altfamilyasına cinsi...
104104  Paracicerina, Cicerininae altfamilyasına cinsi...
104105  Lig futbolcuları Yasin Güreler (d Lig futbolcu...
104106  Elvertia, Kalyptorhynchia seksiyonuna cinsidir...
104107  Kaynakça Ek Hartcher New York: HarperCollins M...

[104108 rows x 1 columns]

In [3]:
import pandas as pd

# CSV dosyasını oku
df = pd.read_csv('cleaned_data.csv')

# Görmek istediğiniz üç sütunu seçin
selected_columns = df[['padded_tokens']]

# Seçilen sütunları tablo olarak görüntüle
print(selected_columns)

# Eğer Jupyter Notebook kullanıyorsanız, daha güzel görüntü için display() fonksiyonunu kullanabilirsiniz:
from IPython.display import display
display(selected_columns)

                                            padded_tokens
0       [2, 59, 42, 4550, 1092, 550, 8528, 1062, 52, 5...
1       [2, 7722, 11428, 2297, 2742, 7395, 1119, 10491...
2       [2, 16306, 1980, 3008, 2431, 22, 6477, 2123, 2...
3       [2, 21, 2146, 3226, 2401, 2836, 3226, 27718, 5...
4       [2, 6, 13, 29132, 2218, 5999, 1977, 6, 24444, ...
...                                                   ...
104103  [2, 60, 1975, 2370, 6546, 4689, 1006, 16, 39, ...
104104  [2, 8149, 2329, 5790, 3930, 16, 39, 6546, 4689...
104105  [2, 5379, 17315, 1048, 19661, 5646, 2070, 12, ...
104106  [2, 3026, 11411, 4475, 16, 3771, 1032, 6728, 1...
104107  [2, 7934, 2548, 2951, 3698, 1023, 14059, 5510,...

[104108 rows x 1 columns]


padded_tokens
0       [2, 59, 42, 4550, 1092, 550, 8528, 1062, 52, 5...
1       [2, 7722, 11428, 2297, 2742, 7395, 1119, 10491...
2       [2, 16306, 1980, 3008, 2431, 22, 6477, 2123, 2...
3       [2, 21, 2146, 3226, 2401, 2836, 3226, 27718, 5...
4       [2, 6, 13, 29132, 2218, 5999, 1977, 6, 24444, ...
...                                                   ...
104103  [2, 60, 1975, 2370, 6546, 4689, 1006, 16, 39, ...
104104  [2, 8149, 2329, 5790, 3930, 16, 39, 6546, 4689...
104105  [2, 5379, 17315, 1048, 19661, 5646, 2070, 12, ...
104106  [2, 3026, 11411, 4475, 16, 3771, 1032, 6728, 1...
104107  [2, 7934, 2548, 2951, 3698, 1023, 14059, 5510,...

[104108 rows x 1 columns]

In [ ]:
from gensim import corpora
from gensim.models import LdaMulticore
import pandas as pd

# CSV dosyasını okuma
df = pd.read_csv('cleaned_data3.csv')

# Verinin bir alt kümesini seçme
df_sample = df.sample(n=10000, random_state=100)

# Kelimeleri token'lara ayırma
tokenized_text = [text.split() for text in df_sample['kısaltılmıs_metin']]

# Dictionary ve Corpus oluşturma
id2word = corpora.Dictionary(tokenized_text)
corpus = [id2word.doc2bow(text) for text in tokenized_text]

# LDA Modelini Eğitme
lda_model = LdaMulticore(
    corpus=corpus,
    id2word=id2word,
    num_topics=5,
    random_state=100,
    chunksize=50,
    passes=5,
    alpha='symmetric',
    eta='auto',
    per_word_topics=True,
    workers=4  # Paralel iş parçacıkları kullanarak performansı artırır
)

# Sonuçları görüntüleme
for idx, topic in lda_model.print_topics(-1):
    print(f"Topic: {idx}\nWords: {topic}\n")

# Alt kümesini kaydetme
df_sample.to_csv('cleaned_processed_data.csv', index=False)


Subheadings belirleme 

In [1]:
from pymongo import MongoClient
from sentence_transformers import SentenceTransformer
import numpy as np 
from sklearn.metrics.pairwise import cosine_similarity
import spacy
import pandas as pd

# Model ve NLP yükleme
model = SentenceTransformer('sentence-transformers/paraphrase-MiniLM-L6-v2')
nlp = spacy.load('en_core_web_sm')

# MongoDB bağlantısı
client = MongoClient("mongodb://localhost:27017/")  
db = client['EgitimDatabase']  
collection = db['test']

# Subheading'leri çıkarma
def extract_subheadings(text):
    doc = nlp(text)
    sentences = [sent.text for sent in doc.sents]
    return sentences

# Metinleri gömme (embedding) işlemi
def embed_text(text):
    return model.encode(text)

# En iyi subheading'leri seçme
def get_top_subheadings(title, keywords, text, top_n=5):
    title_embedding = embed_text(title)
    keywords_embedding = embed_text(' '.join(keywords))
    subheadings = extract_subheadings(text)
    subheadings_embeddings = [embed_text(sub) for sub in subheadings]
    
    scores = [cosine_similarity([title_embedding], [embedding])[0][0] + 
              cosine_similarity([keywords_embedding], [embedding])[0][0]
              for embedding in subheadings_embeddings]
    
    top_indices = np.argsort(scores)[-top_n:]
    top_subheadings = [subheadings[i] for i in top_indices]

    return top_subheadings

# Verileri işleme ve CSV'ye yazma
def process_documents(batch_size=1000, top_n_subheadings=5):
    data = []
    total_documents = 10000
    for skip in range(0, total_documents, batch_size):
        documents = collection.find({}, {'keywords': 1, 'title': 1, 'text': 1}).skip(skip).limit(batch_size)
        for doc in documents:
            title = doc['title']
            keywords = doc['keywords']
            text = doc['text']
            
            top_subheadings = get_top_subheadings(title, keywords, text)
            
            # Verileri listeye ekleyin
            data.append({
                'Title': title,
                'Keywords': ', '.join(keywords),
                'Subheadings': '; '.join(top_subheadings)
            })
        
        # Her batch sonrası CSV dosyasına kaydetme
        df = pd.DataFrame(data)
        df.to_csv('subheadings.csv', index=False, mode='a', header=not bool(skip))
        print(f"Batch {skip // batch_size + 1} işlenip kaydedildi.")
    
    print("Subheadings başarıyla 'subheadings.csv' dosyasına kaydedildi.")

# CSV'ye yazma işlemini başlatma
process_documents()


c:\gitProjects\yeni\.venv\lib\site-packages\sentence_transformers\cross_encoder\CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
c:\gitProjects\yeni\.venv\lib\site-packages\transformers\utils\generic.py:441: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(
c:\gitProjects\yeni\.venv\lib\site-packages\transformers\utils\generic.py:309: FutureWarning: `torch.utils._pytree._register_pytree_node` is deprecated. Please use `torch.utils._pytree.register_pytree_node` instead.
  _torch_pytree._register_pytree_node(
c:\gitProjects\yeni\.venv\lib\site-packages\huggingface_hub\file_download.py:1150: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when po

Batch 1 işlenip kaydedildi.


KeyboardInterrupt: 

In [ ]:


def generate_ngrams(text, n):
    tokens = word_tokenize(text) #["this","is","a","test"]
    n_grams = ngrams(tokens, n) #kelime gruplarına böler
    return [' '.join(gram) for gram in n_grams]

def get_important_ngrams(text, n, top_n=5):
    n_grams = generate_ngrams(text, n)
    ngram_freq = Counter(n_grams)
    most_common_ngrams = [ngram for ngram, _ in ngram_freq.most_common(top_n)]
    return most_common_ngrams

def get_similar_bigrams(text, n=2, similarity_threshold=0.8):
    # Bigramları oluştur
    bigrams = generate_ngrams(text, n)
    
    # Bigramları embedding vektörlerine dönüştür
    bigram_embeddings = [embed_text(bigram) for bigram in bigrams]
    
    # Benzer bigramları listelemek için boş bir liste oluştur
    similar_bigrams = []
    
    # Bigramlar arasındaki benzerlikleri kontrol et
    for i in range(len(bigrams)):
        for j in range(i + 1, len(bigrams)):
            similarity = cosine_similarity([bigram_embeddings[i]], [bigram_embeddings[j]])[0][0]
            if similarity >= similarity_threshold:
                similar_bigrams.append((bigrams[i], bigrams[j], similarity))
    
    return similar_bigrams

similar_bigrams = get_similar_bigrams(text, n=2, similarity_threshold=0.8)
# Benzer bigramları yazdır
for bigram1, bigram2, similarity in similar_bigrams:
    print(f"Bigram 1: {bigram1}, Bigram 2: {bigram2}, Similarity: {similarity:.2f}")

def generate_subheadings(text, num_headings=5):
    # Metni spaCy ile işleyin
    doc = nlp(text)
    
    # Biagram ve triagramları oluşturun
    bigrams = get_important_ngrams(text, 2, top_n=num_headings)
    trigrams = get_important_ngrams(text, 3, top_n=num_headings)
    
    # Subheadings'leri birleştirin
    headings = list(set(bigrams + trigrams))
    
    return headings